# Track observations

Track observations are point observations for moving points. The index therefore consists of time, x- and y-positions. Altimetry data acquired from satellite is an example of track observations; data obtained from boat is another example. 

The track observation data may come from a file or web api. We will cover the following situations here: 

* File
    - dfs0
    - csv/excel
* REST API

modelskill has the class `TrackObservation` for working with track observations. 

Track observations consist of time-**position**-value (data) and *meta* data such as

* data type (e.g. water level)
* unit (e.g. meter)

ModelSkill is agnostic to the coordinate reference system (CRS) and it is therefore the responsibility of the user to make sure that all data (observations and model) use the same CRS.

In [1]:
import pandas as pd
import modelskill as ms

## Data from file

The two first items in the file must be x- and y- coordinate values. 

**dfs0** files can be read directly by TrackObservation. 

**csv** files needs to be read by pandas first and passed to TrackObservation as a DataFrame. 

In [2]:
fn = "data/SW/altimetry_NorthSea_20171027.csv"
df = pd.read_csv(fn, index_col=0, parse_dates=True)  # step 1: create DataFrame
df.head()

lon        lat  surface_elevation  \
date                                                          
2017-10-26 04:37:37  8.757272  53.926136             1.6449   
2017-10-26 04:37:54  8.221631  54.948459             1.1200   
2017-10-26 04:37:55  8.189390  55.008547             1.0882   
2017-10-26 04:37:56  8.157065  55.068627             1.0309   
2017-10-26 04:37:58  8.124656  55.128700             1.0369   

                     significant_wave_height  wind_speed  
date                                                      
2017-10-26 04:37:37                    0.426    6.100000  
2017-10-26 04:37:54                    1.634    9.030000  
2017-10-26 04:37:55                    1.717    9.370000  
2017-10-26 04:37:56                    1.869    9.559999  
2017-10-26 04:37:58                    1.939    9.980000

In [3]:
o1 = ms.TrackObservation(df, item="surface_elevation")  # step 2: create TrackObservation
o1

/home/jan/src/book-learn-mikeio-fmskill/.venv/lib/python3.10/site-packages/modelskill/timeseries/_track.py:135: UserWarning: Removed 22 duplicate timestamps with keep=first
  warnings.warn(


TrackObservation: surface_elevation, n=1093

## DHI Altimetry API

You need to pip install "watobs" for this part!

See [Altimetry_data.ipynb](https://nbviewer.jupyter.org/github/DHI/watobs/blob/main/notebooks/Altimetry_data.ipynb) example notebook.


In [6]:
import os
from watobs import DHIAltimetryRepository

In [7]:
api_key = os.environ["DHI_ALTIMETRY_API_KEY"]
repo = DHIAltimetryRepository(api_key)

KeyError: 'DHI_ALTIMETRY_API_KEY'

In [ ]:
data = repo.get_altimetry_data(area="lon=2.9&lat=53.9&radius=100", start_time="2019-10-1", 
end_time="2019-10-8")
data.df.head()

In [ ]:
data.plot_map()

In [8]:
o1 = ms.TrackObservation(data.df, item="significant_wave_height", name='Alti_from_df', quantity=ms.Quantity("Significant wave height", "m"))
o1

NameError: name 'data' is not defined

Or you can save the data to a dfs0 first...

In [ ]:
data.to_dfs0('alti_NS_20191001.dfs0')

In [ ]:
o2 = ms.TrackObservation('alti_NS_20191001.dfs0', item="Significant Wave Height", quantity=ms.Quantity("Significant wave height", "m")
o2